### Importing libraries...

In [1]:
import requests
from pymongo import MongoClient
import pandas as pd
import re
import json
from pandas.io.json import json_normalize
import os
import numpy as np
import math
from folium import Map, Marker, Icon, FeatureGroup, LayerControl, Choropleth
from folium.plugins import HeatMap
from haversine import haversine, Unit

### Importing Companies Data

In [2]:
dbName = "companies.json"
mongodbURL = f"mongodb://localhost/{dbName}"

client = MongoClient(mongodbURL, connectTimeoutMS=2000, serverSelectionTimeoutMS=2000)
db = client.get_database()

### Verifying amount of companies of potential chosen country

In [3]:
data = db.companies.aggregate([{"$group":{"_id":"$offices.country_code","count":{"$sum":1}}}])
countries = list(data)

In [4]:
county_counts=[]
for x in countries:
    county_counts.append(x['_id'])


In [5]:
county_counts = [c for n in county_counts for c in n]


In [6]:
from collections import Counter
county_counts = Counter(county_counts)
{k: v for k, v in sorted(county_counts.items(), key=lambda item: item[1], reverse=True)}

{'USA': 775,
 'GBR': 257,
 'DEU': 116,
 'IND': 106,
 'FRA': 82,
 'AUS': 80,
 'CHN': 79,
 'ESP': 62,
 'CAN': 62,
 'JPN': 52,
 'SGP': 46,
 'NLD': 40,
 'SWE': 35,
 'CHE': 31,
 'BRA': 30,
 'ARG': 29,
 'ISR': 28,
 'ITA': 28,
 'HKG': 25,
 'IRL': 25,
 'RUS': 23,
 'TWN': 20,
 'BEL': 19,
 'MEX': 18,
 'NOR': 17,
 'DNK': 16,
 'KOR': 15,
 'NZL': 15,
 'ROM': 15,
 'ZAF': 15,
 'PHL': 15,
 'ARE': 14,
 'MYS': 14,
 'AUT': 14,
 'POL': 13,
 'PRT': 12,
 'FIN': 12,
 'UKR': 12,
 'CZE': 11,
 'TUR': 11,
 'CHL': 9,
 'VNM': 9,
 'BGR': 8,
 'GRC': 7,
 'THA': 6,
 'SVN': 6,
 'COL': 6,
 'EST': 5,
 'ANT': 5,
 'HUN': 5,
 'EGY': 5,
 'LKA': 4,
 'LVA': 4,
 'HRV': 4,
 'PAK': 4,
 'CYP': 4,
 'JOR': 3,
 'MAR': 3,
 'SAU': 3,
 'LTU': 3,
 'URY': 3,
 'NGA': 3,
 'BGD': 3,
 'IDN': 3,
 'MKD': 3,
 'LUX': 3,
 'MLT': 3,
 'MUS': 2,
 'BIH': 2,
 'LBN': 2,
 'ISL': 2,
 'GIB': 2,
 'PAN': 2,
 'VEN': 2,
 'PRK': 2,
 'CSS': 2,
 'NIC': 2,
 'ARA': 2,
 'VGB': 2,
 'KEN': 2,
 'QAT': 2,
 'UZB': 2,
 'TUN': 1,
 'DOM': 1,
 'SDN': 1,
 'PER': 1,
 'GHA': 1,

**Countries which companies I have more information of:**  
  
USA 🇺🇸  
GBR 🇬🇧  
DEU 🇩🇪   
IND 🇮🇪  
FRA 🇫🇷  

**Top Videogame development Countries:**

USA 🇺🇸 = 194  
GBR 🇬🇧 =  48  
DEU 🇩🇪 =   /  
IND 🇮🇪  =   /  
FRA 🇫🇷 =  23  

**Chosen Country:  
US** 🇺🇸 🇺🇸 🇺🇸 🇺🇸

## Location

**Requisite:**  
Developers like to be near successful tech startups that have raised at least 1 Million dollars.

**Query:**  
 - Country: USA  
 - Is a startup: founded after 2007 
 - Tech categories: software, design, games_video, web, mobile
 - Raised at least 1 Million dollars 
 

In [7]:
query = {"$and":[
    {"offices.country_code":"USA"},
    {"founded_year":{"$gte":2007}},
    {"funding_rounds.raised_amount":{"$gte":1000000}},
    {"category_code":{"$in":["software","design","games_video","web", "mobile"]}},
]}
cur = db.companies.find(query)
df = pd.DataFrame(list(cur))
df

_id                name           permalink  \
0    52cdef7c4bab8bd675297da9              Mahalo              mahalo   
1    52cdef7c4bab8bd675297dc2        AdaptiveBlue        adaptiveblue   
2    52cdef7c4bab8bd675297dc0          Livestream          livestream   
3    52cdef7c4bab8bd675297dc1             Ustream             ustream   
4    52cdef7c4bab8bd675297dd1            SodaHead            sodahead   
..                        ...                 ...                 ...   
294  52cdef7f4bab8bd67529c4f0         Culture Jam         culture-jam   
295  52cdef7f4bab8bd67529c55b   Clavis Technology   clavis-technology   
296  52cdef7f4bab8bd67529c59b  Luma International  luma-international   
297  52cdef7f4bab8bd67529c5b8   Continuity Engine   continuity-engine   
298  52cdef7f4bab8bd67529c679   Bump Technologies   bump-technologies   

                                        crunchbase_url  \
0             http://www.crunchbase.com/company/mahalo   
1       http://www.crunchbase.com/company/adaptiveblue   
2         http://www.crunchbase.com/company/livestream   
3            http://www.crunchbase.com/company/ustream   
4           http://www.crunchbase.com/company/sodahead   
..                                                 ...   
294      http://www.crunchbase.com/company/culture-jam   
295  http://www.crunchbase.com/company/clavis-techn...   
296  http://www.crunchbase.com/company/luma-interna...   
297  http://www.crunchbase.com/company/continuity-e...   
298  http://www.crunchbase.com/company/bump-technol...   

                        homepage_url                               blog_url  \
0                  http://mahalo.com                http://blog.mahalo.com/   
1             http://www.getglue.com           http://blog.adaptiveblue.com   
2          http://www.livestream.com        http://www.livestream.com/blog/   
3              http://www.ustream.tv            http://www.ustream.com/blog   
4                http://sodahead.com                                          
..                               ...                                    ...   
294         http://site.promojam.com            http://promojam.tumblr.com/   
295  http://www.clavistechnology.com   http://www.clavistechnology.com/news   
296       http://www.lumacentral.com            http://blog.lumacentral.com   
297        http://www.continuity.net  http://continuityengine.blogspot.com/   
298                     http://bu.mp                     http://blog.bu.mp/   

                                 blog_feed_url twitter_username category_code  \
0                 http://blog.mahalo.com/feed/     MahaloDotCom           web   
1      http://blog.adaptiveblue.com/?feed=rss2          GetGlue   games_video   
2    http://www.livestream.com/blog/?feed=rss2       livestream   games_video   
3             http://www.ustream.com/blog/feed          USTREAM   games_video   
4                                                      SodaHead           web   
..                                         ...              ...           ...   
294                                                  culturejam           web   
295      http://www.clavistechnology.com/feed/       Clavistech      software   
296       http://blog.lumacentral.com/atom.xml      lumacentral      software   
297                                               ContinuityEng      software   
298                                                    bumptech        mobile   

     number_of_employees  ...  investments  \
0                   40.0  ...           []   
1                   15.0  ...           []   
2                  120.0  ...           []   
3                  250.0  ...           []   
4                   25.0  ...           []   
..                   ...  ...          ...   
294                 15.0  ...           []   
295                 50.0  ...           []   
296                 40.0  ...           []   
297                 11.0  ...           []   
298                  NaN

In [8]:
df.columns

Index(['_id', 'name', 'permalink', 'crunchbase_url', 'homepage_url',
       'blog_url', 'blog_feed_url', 'twitter_username', 'category_code',
       'number_of_employees', 'founded_year', 'founded_month', 'founded_day',
       'deadpooled_year', 'deadpooled_month', 'deadpooled_day',
       'deadpooled_url', 'tag_list', 'alias_list', 'email_address',
       'phone_number', 'description', 'created_at', 'updated_at', 'overview',
       'image', 'products', 'relationships', 'competitions', 'providerships',
       'total_money_raised', 'funding_rounds', 'investments', 'acquisition',
       'acquisitions', 'offices', 'milestones', 'ipo', 'video_embeds',
       'screenshots', 'external_links', 'partners'],
      dtype='object')

In [9]:
offices = df[["name", "offices"]].explode("offices")
offices

name                                            offices
0                Mahalo  {'description': '', 'address1': '3525 Eastham ...
1          AdaptiveBlue  {'description': '', 'address1': '131 Varick St...
2            Livestream  {'description': 'Livestream HQ', 'address1': '...
3               Ustream  {'description': 'San Francisco Office', 'addre...
3               Ustream  {'description': 'Los Angeles Office', 'address...
..                  ...                                                ...
296  Luma International  {'description': 'HQ North America', 'address1'...
296  Luma International  {'description': 'Office France', 'address1': '...
296  Luma International  {'description': 'Office The Netherlands', 'add...
297   Continuity Engine  {'description': 'HQ', 'address1': '150 Munson ...
298   Bump Technologies  {'description': 'HQ', 'address1': '', 'address...

[393 rows x 2 columns]

In [10]:
offices = json_normalize(json.loads(offices.to_json(orient="records")))
offices = offices[["name", "offices.latitude", "offices.longitude", "offices.state_code"]]
offices

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """Entry point for launching an IPython kernel.


name  offices.latitude  offices.longitude  \
0                Mahalo         34.017606        -118.487267   
1          AdaptiveBlue         40.801358         -74.337200   
2            Livestream         40.726155         -73.995625   
3               Ustream         37.392936        -122.079480   
4               Ustream               NaN                NaN   
..                  ...               ...                ...   
388  Luma International               NaN                NaN   
389  Luma International               NaN                NaN   
390  Luma International               NaN                NaN   
391   Continuity Engine         41.327918         -73.243552   
392   Bump Technologies               NaN                NaN   

    offices.state_code  
0                   CA  
1                   NY  
2                   NY  
3                   CA  
4                   CA  
..                 ...  
388                 CA  
389               None  
390               None  
391                 CT  
392                 CA  

[393 rows x 4 columns]

In [11]:
offices["offices.state_code"].value_counts()

CA    184
NY     50
MA     23
WA     11
CO      9
TX      9
VA      7
NC      5
FL      5
IL      5
PA      4
CT      3
UT      3
GA      3
OR      3
AZ      2
NJ      2
MN      2
MD      2
RI      1
DC      1
LA      1
ME      1
SC      1
KY      1
NH      1
Name: offices.state_code, dtype: int64

### Chosen state: California

In [12]:
offices = offices.loc[offices["offices.state_code"] == "CA"]
offices = offices.dropna()
offices = offices.reset_index()
offices = offices.drop(columns = ["index"])

In [13]:
offices

name  offices.latitude  offices.longitude  \
0                  Mahalo         34.017606        -118.487267   
1                 Ustream         37.392936        -122.079480   
2                SodaHead         37.269175        -119.306607   
3            Funny Or Die         37.421621        -122.137444   
4                 Seesmic         37.775196        -122.419204   
..                    ...               ...                ...   
138  Global Fitness Media         34.054318        -118.462876   
139           CrowdGather         34.168955        -118.575293   
140       High Gear Media         37.445335        -122.158330   
141               Teambox         41.406335           2.192023   
142           Culture Jam         34.013715        -118.466060   

    offices.state_code  
0                   CA  
1                   CA  
2                   CA  
3                   CA  
4                   CA  
..                 ...  
138                 CA  
139                 CA  
140                 CA  
141                 CA  
142                 CA  

[143 rows x 4 columns]

In [14]:
offices = offices.rename(columns={"name": "Name", "offices.latitude": "Latitude", "offices.longitude": "Longitude", "offices.state_code": "State Code"})

In [15]:
offices

Name   Latitude   Longitude State Code
0                  Mahalo  34.017606 -118.487267         CA
1                 Ustream  37.392936 -122.079480         CA
2                SodaHead  37.269175 -119.306607         CA
3            Funny Or Die  37.421621 -122.137444         CA
4                 Seesmic  37.775196 -122.419204         CA
..                    ...        ...         ...        ...
138  Global Fitness Media  34.054318 -118.462876         CA
139           CrowdGather  34.168955 -118.575293         CA
140       High Gear Media  37.445335 -122.158330         CA
141               Teambox  41.406335    2.192023         CA
142           Culture Jam  34.013715 -118.466060         CA

[143 rows x 4 columns]

In [16]:
m = Map(location=[37.794020, -122.403124],zoom_start=4)
for i, row in offices.iterrows():
    icon = Icon(
            color="red",
            prefix="fa",
            icon="trophy")
    Marker(
        location=row[["Latitude","Longitude"]],
        tooltip=row["Name"],
        icon=icon
    ).add_to(m)
m

In [17]:
#Eliminate not in California: 
intruders = ["GENWI", "Zinch", "Filtrbox", "Titan Gaming", "DotBlu", "Formspring", "ChessPark", "Socialize", "Fortumo", "Zendesk", "XIHA", "Teambox"]
for name in intruders: 
    offices = offices[offices.Name != name]

In [18]:
m = Map(location=[35.794020, -120.403124],zoom_start=7)
for i, row in offices.iterrows():
    icon = Icon(
            color="red",
            prefix="fa",
            icon="fa-building")
    Marker(
        location=row[["Latitude","Longitude"]],
        tooltip=row["Name"],
        icon=icon
    ).add_to(m)
m

## Google API

In [19]:
from dotenv import load_dotenv
load_dotenv()
apiKey = os.getenv("google_key")
url = f"https://maps.googleapis.com/maps/api/place/textsearch/json?query=starbucks+in+CA&key={apiKey}"
res = requests.get(url)


In [20]:
res = res.json()

In [21]:
from dotenv import load_dotenv
load_dotenv()
apiKey = os.getenv("google_key")
url = "https://maps.googleapis.com/maps/api/place/textsearch/json"
#query=starbucks+in+CA&key={apiKey}&pageToken=res['next_page_token']"
res = requests.get(url)
res = res.json()

In [22]:
def getData(query, page_token=None):
    url = "https://maps.googleapis.com/maps/api/place/textsearch/json"
    params = {"key":os.getenv("google_key"), "query":query}
    if page_token:
        params["pageToken"]=page_token
    res = requests.get(url, params=params)
    res = res.json()
    results = res["results"]
    if 'next_page_token' in res.keys():
        page_token = res['next_page_token']
        results=[results, page_token]
    else: 
        results=[results,False]
    return results

In [23]:
def getLocations(query, limit=50):
    data = []
    page_token = None
    while len(data)<limit:
        results, page_token = getData(query, page_token)
        data+=results
        if not page_token: 
            break
    return data

##  Function to calculate distances in km

**Latitude:** 1 deg = 110.574 km.   
**Longitude:** 1 deg = 111.320*cos(latitude) km.

In [24]:
'''
def FindDistances(req):
    d=[]
    for i in offices.index:
        d_list=[]
        for ind in req.index: 
            x = req['Latitude'][ind]
            y = req['Longitude'][ind] 
            distance = (((x-(offices['Latitude'][i]))**2)+((y-(offices['Longitude'][i]))**2))**(1/2)
            d_list.append(distance)
        d.append(min(d_list))
    offices['New'] = d
'''

"\ndef FindDistances(req):\n    d=[]\n    for i in offices.index:\n        d_list=[]\n        for ind in req.index: \n            x = req['Latitude'][ind]\n            y = req['Longitude'][ind] \n            distance = (((x-(offices['Latitude'][i]))**2)+((y-(offices['Longitude'][i]))**2))**(1/2)\n            d_list.append(distance)\n        d.append(min(d_list))\n    offices['New'] = d\n"

In [41]:
def FindDistances(req):
    d=[]
    lat=[]
    long=[]
    office=[]
    for i in offices.index:
        d_list=[]
        lat_list=[]
        long_list=[]
        office_list=[]
        for ind in req.index: 
            x = req['Latitude'][ind]
            y = req['Longitude'][ind]
            req_loc=(x,y)
            office_loc=(offices['Latitude'][i], offices['Longitude'][i])         
            distance = haversine(req_loc, office_loc)
            d_list.append(distance)
            lat_list.append(x)
            long_list.append(y)
            office_list.append(offices['Name'][i])
        d.append(min(d_list))
        lat.append(lat_list[d_list.index(min(d_list))])
        long.append(long_list[d_list.index(min(d_list))])
        office.append(office_list[d_list.index(min(d_list))])
    requisito = pd.DataFrame(
    {'New Distance': d,
     'New Latitude': lat,
     'New Longitude': long,
     'Name': office
    })
    return requisito

## Starbucks

**Requisite:**  
Executives like Starbucks A LOT. Ensure there's a starbucks not to far.

In [26]:
data = getLocations("starbucks in CA", 100)
dataset = pd.DataFrame(data)

In [27]:
starbucks = []
for st in dataset["geometry"]:
    new_dict={}
    new_dict["Latitude"]= st['location']['lat']
    new_dict["Longitude"]= st['location']['lng']
    starbucks.append(new_dict)

In [28]:
starbucks = pd.DataFrame(starbucks)
starbucks

Latitude   Longitude
0   34.072428 -117.881891
1   37.291159 -121.989834
2   37.762265 -121.433395
3   38.714409 -120.839673
4   38.762384 -120.576595
..        ...         ...
95  34.136023 -118.132490
96  34.890722 -116.999380
97  37.969738 -121.289320
98  33.649162 -117.830863
99  38.013442 -121.868315

[100 rows x 2 columns]

In [29]:
starbucks = FindDistances(starbucks)

In [30]:
offices = offices.merge(starbucks, on='Name')
offices = offices.rename(columns={"New Distance":"Starbucks Distance", "New Latitude":"Starbucks Latitude", "New Longitude":"Starbucks Longitude"})

In [31]:
offices

Name   Latitude   Longitude State Code  \
0                  Mahalo  34.017606 -118.487267         CA   
1                 Ustream  37.392936 -122.079480         CA   
2                SodaHead  37.269175 -119.306607         CA   
3            Funny Or Die  37.421621 -122.137444         CA   
4                 Seesmic  37.775196 -122.419204         CA   
..                    ...        ...         ...        ...   
142            Moviepilot  34.052234 -118.243685         CA   
143  Global Fitness Media  34.054318 -118.462876         CA   
144           CrowdGather  34.168955 -118.575293         CA   
145       High Gear Media  37.445335 -122.158330         CA   
146           Culture Jam  34.013715 -118.466060         CA   

     Starbucks Distance  Starbucks Latitude  Starbucks Longitude  
0             25.747623           34.072428          -117.881891  
1              6.841138           37.291159          -121.989834  
2            152.560395           37.291159          -121.989834  
3              0.827533           38.714409          -120.839673  
4              2.358045           38.714409          -120.839673  
..                  ...                 ...                  ...  
142           11.859684           37.451659          -121.921435  
143           21.571646           37.451659          -121.921435  
144           28.627026           37.451659          -121.921435  
145            2.407823           37.451659          -121.921435  
146           24.500504           37.451659          -121.921435  

[147 rows x 7 columns]

In [32]:
m = Map(location=[35.794020, -120.403124],zoom_start=7)
for i, row in offices.iterrows():
    icon = Icon(
            color="red",
            prefix="fa",
            icon="fa-building")
    Marker(
        location=row[["Latitude","Longitude"]],
        icon=icon
    ).add_to(m)
    
for i, row in offices.iterrows():
    icon = Icon(
            color="green",
            prefix="fa",
            icon="fa-coffee")
    Marker(
        location=row[["Starbucks Latitude","Starbucks Longitude"]],
        icon=icon
    ).add_to(m)
m

## Airports

**Requisite:**  
Account managers need to travel a lot.

In [33]:
data = getLocations("Airport in California", 100)
airportset = pd.DataFrame(data)

In [34]:
airportset

business_status                                  formatted_address  \
0      OPERATIONAL  1 World Way, Los Angeles, CA 90045, United States   
1      OPERATIONAL             San Francisco, CA 94128, United States   
2      OPERATIONAL  18601 Airport Way, Santa Ana, CA 92707, United...   
3      OPERATIONAL                   Ontario, CA 91761, United States   
4      OPERATIONAL  6900 Airport Blvd, Sacramento, CA 95837, Unite...   
..             ...                                                ...   
95     OPERATIONAL  12653 Osborne St, Pacoima, CA 91331, United St...   
96     OPERATIONAL  3400 E Tahquitz Canyon Way, Palm Springs, CA 9...   
97     OPERATIONAL  500 James Fowler Rd, Santa Barbara, CA 93117, ...   
98     OPERATIONAL  550 Sally Ride Dr, Concord, CA 94520, United S...   
99     OPERATIONAL  16461 Sherman Way, Van Nuys, CA 91406, United ...   

                                             geometry  \
0   {'location': {'lat': 33.9415889, 'lng': -118.4...   
1   {'location': {'lat': 37.6213129, 'lng': -122.3...   
2   {'location': {'lat': 33.6761901, 'lng': -117.8...   
3   {'location': {'lat': 34.0559781, 'lng': -117.5...   
4   {'location': {'lat': 38.6950854, 'lng': -121.5...   
..                                                ...   
95  {'location': {'lat': 34.2598054, 'lng': -118.4...   
96  {'location': {'lat': 33.8303194, 'lng': -116.5...   
97  {'location': {'lat': 34.4271935, 'lng': -119.8...   
98  {'location': {'lat': 37.9902157, 'lng': -122.0...   
99  {'location': {'lat': 34.2096399, 'lng': -118.4...   

                                                 icon  \
0   https://maps.gstatic.com/mapfiles/place_api/ic...   
1   https://maps.gstatic.com/mapfiles/place_api/ic...   
2   https://maps.gstatic.com/mapfiles/place_api/ic...   
3   https://maps.gstatic.com/mapfiles/place_api/ic...   
4   https://maps.gstatic.com/mapfiles/place_api/ic...   
..                                                ...   
95  https://maps.gstatic.com/mapfiles/place_api/ic...   
96  https://maps.gstatic.com/mapfiles/place_api/ic...   
97  https://maps.gstatic.com/mapfiles/place_api/ic...   
98  https://maps.gstatic.com/mapfiles/place_api/ic...   
99  https://maps.gstatic.com/mapfiles/place_api/ic...   

                                          id  \
0   2b1ad644609c86ef8156eeec48a4675d580224d9   
1   9c9fb107d7a776c3f6a26791b07982d7db079113   
2   da9ed12835b3a597d4bcbc961a779ab353b0d145   
3   ec4d4162373ff66e9c6628eec8b410c40019d703   
4   b825239c5bd3448da42434d6402297b961b445a2   
..                                       ...   
95  a27abbb55ffe476125745b8c7eed9c0eac4c7823   
96  2f3d34371900b038e82bf59a7ac235eaff50802a   
97  2d04db686a2c2a47941cc5841bd491ecd3b5a34e   
98  3a6ea41c90253d47c284cf8e55b0ba6fbd18fabc   
99  7008e7155542e7d08b9a3b10d9e6f6d4b0a53df8   

                                   name  \
0     Los Angeles International Airport   
1   San Francisco International Airport   
2                    John Wayne Airport   
3         Ontario International Airport   
4      Sacramento International Airport   
..                                  ...   
95                     Whiteman Airport   
96   Palm Springs International Airport   
97                Santa Barbara Airport   
98               Buchanan Field Airport   
99                     Van Nuys Airport   

                                               photos  \
0   [{'height': 3024, 'html_attributions': ['<a hr...   
1   [{'height': 3024, 'html_attributions': ['<a hr...   
2   [{'height': 3024, 'html_attributions': ['<a hr...   
3   [{'height': 3021, 'html_attributions': ['<a hr...   
4   [{'height': 2268, 'html_attributions': ['<a hr...   
..                                                ...   
95  [{'height': 1489, 'html_attributions': ['<a hr...   
96  [{'height': 3024, 'html_attributions': ['<a hr...   
97  [{'height': 1365, 'html_attributions': ['<a hr...   
98  [{'height': 3024, 'html_attributions': ['<a hr...   
99  [{'height': 720, 'html_attribut

In [35]:
airports = []
for a in airportset["geometry"]:
    new_dict={}
    new_dict["Latitude"]= a['location']['lat']
    new_dict["Longitude"]= a['location']['lng']
    airports.append(new_dict)

In [38]:
airports = pd.DataFrame(airports)
airports

Latitude   Longitude
0   33.941589 -118.408530
1   37.621313 -122.378955
2   33.676190 -117.867476
3   34.055978 -117.598057
4   38.695085 -121.590065
..        ...         ...
95  34.259805 -118.411929
96  33.830319 -116.507047
97  34.427194 -119.839883
98  37.990216 -122.056132
99  34.209640 -118.489645

[100 rows x 2 columns]

In [42]:
airports = FindDistances(airports)

In [43]:
offices = offices.merge(airports, on='Name')
offices = offices.rename(columns={"New Distance":"Airport Distance", "New Latitude":"Airport Latitude", "New Longitude":"Airport Longitude"})

In [44]:
offices

Name   Latitude   Longitude State Code  \
0                  Mahalo  34.017606 -118.487267         CA   
1                 Ustream  37.392936 -122.079480         CA   
2                SodaHead  37.269175 -119.306607         CA   
3            Funny Or Die  37.421621 -122.137444         CA   
4                 Seesmic  37.775196 -122.419204         CA   
..                    ...        ...         ...        ...   
238            Moviepilot  34.052234 -118.243685         CA   
239  Global Fitness Media  34.054318 -118.462876         CA   
240           CrowdGather  34.168955 -118.575293         CA   
241       High Gear Media  37.445335 -122.158330         CA   
242           Culture Jam  34.013715 -118.466060         CA   

     Starbucks Distance  Starbucks Latitude  Starbucks Longitude  \
0             25.747623           34.072428          -117.881891   
1              6.841138           37.291159          -121.989834   
2            152.560395           37.291159          -121.989834   
3              0.827533           38.714409          -120.839673   
4              2.358045           38.714409          -120.839673   
..                  ...                 ...                  ...   
238           11.859684           37.451659          -121.921435   
239           21.571646           37.451659          -121.921435   
240           28.627026           37.451659          -121.921435   
241            2.407823           37.451659          -121.921435   
242           24.500504           37.451659          -121.921435   

     Airport Distance  Airport Latitude  Airport Longitude  
0           11.142608         33.941589        -118.408530  
1           13.686980         37.363947        -121.928938  
2           65.906729         36.775849        -119.718108  
3           19.504627         37.363947        -121.928938  
4           17.473626         37.621313        -122.378955  
..                ...               ...                ...  
238         19.323868         34.198312        -118.357404  
239         13.499050         33.941589        -118.408530  
240          9.084407         34.209640        -118.489645  
241         22.191320         37.363947        -121.928938  
242          9.615726         33.941589        -118.408530  

[243 rows x 10 columns]

In [45]:
m = Map(location=[35.794020, -120.403124],zoom_start=7)
for i, row in offices.iterrows():
    icon = Icon(
            color="red",
            prefix="fa",
            icon="fa-building")
    Marker(
        location=row[["Latitude","Longitude"]],
        tooltip=row["Name"],
        icon=icon
    ).add_to(m)
    
for i, row in offices.iterrows():
    icon = Icon(
            color="blue",
            prefix="fa",
            icon="fa-plane")
    Marker(
        location=row[["Airport Latitude","Airport Longitude"]],
        icon=icon
    ).add_to(m)
    
m

## Schools

In [46]:
data = getLocations("School in California", 100)
schoolset = pd.DataFrame(data)

In [47]:
schools = []
for s in schoolset["geometry"]:
    new_dict={}
    new_dict["Latitude"]= s['location']['lat']
    new_dict["Longitude"]= s['location']['lng']
    schools.append(new_dict)

In [48]:
schools = pd.DataFrame(schools)
schools

Latitude   Longitude
0   40.476588   -3.853554
1   33.878099 -118.054286
2   33.861031 -118.254754
3   33.688892 -117.925587
4   33.805531 -117.841449
..        ...         ...
95  32.882748 -117.222179
96  34.123312 -117.738770
97  37.848269 -122.239620
98  33.608324 -117.268230
99  34.657081 -120.102124

[100 rows x 2 columns]

In [49]:
schools = FindDistances(schools)

In [50]:
offices = offices.merge(schools, on='Name')
offices = offices.rename(columns={"New Distance":"School Distance", "New Latitude":"School Latitude", "New Longitude":"School Longitude"})

In [52]:
m = Map(location=[35.794020, -120.403124],zoom_start=7)
for i, row in offices.iterrows():
    icon = Icon(
            color="red",
            prefix="fa",
            icon="fa-building")
    Marker(
        location=row[["Latitude","Longitude"]],
        tooltip=row["Name"],
        icon=icon
    ).add_to(m)
    
for i, row in offices.iterrows():
    icon = Icon(
            color="orange",
            prefix="fa",
            icon="fa-child")
    Marker(
        location=row[["School Latitude","School Longitude"]],
        icon=icon
    ).add_to(m)
    
m

## Average of distances

**Importance**  
  
Considering the employees will have to take a cab to go to the airport or take their kids to school.   
It would be nice to have a starbucks at a walking distance, therefore I will get rid of any offices which's distance to a starbucks or a bar is greater than 


In [53]:
offices

Name   Latitude   Longitude State Code  \
0                   Mahalo  34.017606 -118.487267         CA   
1                  Ustream  37.392936 -122.079480         CA   
2                 SodaHead  37.269175 -119.306607         CA   
3             Funny Or Die  37.421621 -122.137444         CA   
4                  Seesmic  37.775196 -122.419204         CA   
...                    ...        ...         ...        ...   
2158            Moviepilot  34.052234 -118.243685         CA   
2159  Global Fitness Media  34.054318 -118.462876         CA   
2160           CrowdGather  34.168955 -118.575293         CA   
2161       High Gear Media  37.445335 -122.158330         CA   
2162           Culture Jam  34.013715 -118.466060         CA   

      Starbucks Distance  Starbucks Latitude  Starbucks Longitude  \
0              25.747623           34.072428          -117.881891   
1               6.841138           37.291159          -121.989834   
2             152.560395           37.291159          -121.989834   
3               0.827533           38.714409          -120.839673   
4               2.358045           38.714409          -120.839673   
...                  ...                 ...                  ...   
2158           11.859684           37.451659          -121.921435   
2159           21.571646           37.451659          -121.921435   
2160           28.627026           37.451659          -121.921435   
2161            2.407823           37.451659          -121.921435   
2162           24.500504           37.451659          -121.921435   

      Airport Distance  Airport Latitude  Airport Longitude  School Distance  \
0            11.142608         33.941589        -118.408530        27.626121   
1            13.686980         37.363947        -121.928938        11.957623   
2            65.906729         36.775849        -119.718108        64.131314   
3            19.504627         37.363947        -121.928938         8.397413   
4            17.473626         37.621313        -122.378955         7.470377   
...                ...               ...                ...              ...   
2158         19.323868         34.198312        -118.357404        14.022498   
2159         13.499050         33.941589        -118.408530        28.816475   
2160          9.084407         34.209640        -118.489645        41.285516   
2161         22.191320         37.363947        -121.928938         9.110941   
2162          9.615726         33.941589        -118.408530        25.850385   

      School Latitude  School Longitude  
0           33.861031       -118.254754  
1           37.375907       -122.213111  
2           36.810279       -119.744282  
3           37.375907       -122.213111  
4           37.730442       -122.482576  
...               ...               ...  
2158        34.134761       -118.128540  
2159        33.861031       -118.254754  
2160        34.134761       -118.128540  
2161        37.375907       -122.213111  
2162        33.861031       -118.254754  

[2163 rows x 13 columns]

In [50]:
offices["Sum of Distances"] = offices["Starbucks"]+offices["Airport"]+offices["School"]

In [60]:
chosen_offices = offices.sort_values(by=["Starbucks"]).head(10)
chosen_offices = chosen_offices.reset_index()
chosen_offices = chosen_offices.drop(columns = ["index"])

In [94]:
chosen_offices

Name   Latitude   Longitude State Code  Starbucks  \
0       PicApp  37.794020 -122.403124         CA   0.344284   
1     DanceJam  37.781557 -122.407959         CA   0.663812   
2       Gydget  37.791733 -122.398398         CA   0.728794   
3      Elastra  37.791137 -122.391843         CA   0.763823   
4  Crunchyroll  37.781265 -122.393229         CA   1.051495   
5   Reframe It  37.782163 -122.400591         CA   1.178100   
6         Yola  37.791115 -122.395475         CA   1.186358   
7     Tapulous  37.444332 -122.161018         CA   1.365390   
8    99designs  37.795531 -122.400598         CA   1.912817   
9         Milo  37.444531 -122.163352         CA   2.179767   

   Starbucks Latitude  Starbucks Longitude     Airport  Airport Latitude  \
0           37.099098          -121.015467   25.851200         37.363947   
1           35.368092          -119.044988   17.814970         38.695085   
2           35.368092          -119.044988   24.103978         38.695085   
3           35.368092          -119.044988   24.038719         35.149409   
4           35.368092          -119.044988   17.965814         38.695085   
5           37.099098          -121.015467   18.098246         37.363947   
6           35.368092          -119.044988   23.770442         38.695085   
7           35.368092          -119.044988  156.447486         33.950544   
8           35.368092          -119.044988   27.531949         35.149409   
9           37.099098          -121.015467  157.300434         37.363947   

   Airport Longitude      School  School Latitude  School Longitude  \
0        -121.928938   63.863450        37.848269       -122.239620   
1        -121.590065   48.232033        33.805531       -117.841449   
2        -121.590065   61.456369        37.848269       -122.239620   
3        -118.015890   61.427216        37.848269       -122.239620   
4        -121.590065   49.526711        33.805531       -117.841449   
5        -121.928938   49.729574        37.848269       -122.239620   
6        -121.590065   60.999134        33.805531       -117.841449   
7        -117.445930  259.742299        37.848269       -122.239620   
8        -118.015890   66.114315        37.848269       -122.239620   
9        -121.928938  260.675778        37.848269       -122.239620   

   Sum of Distances  
0         90.058934  
1         66.710816  
2         86.289142  
3         86.229758  
4         68.544020  
5         69.005920  
6         85.955933  
7        417.555175  
8         95.559081  
9        420.155979

In [82]:

m = Map(location=[35.794020, -120.403124],zoom_start=7)
"""
def mapping(req="", icon=None, color="red"):
    for i, row in chosen_offices.iterrows():
        icon = Icon(
                color=color,
                prefix="fa",
                icon=f"fa-{i}")
        Marker(
            location=row[[f"{req}Latitude",f"{req}Longitude"]],
            tooltip=row["Name"],
            icon=icon
        ).add_to(m)
"""

In [91]:
m = Map(location=[35.794020, -120.403124],zoom_start=7)
for i, row in chosen_offices.iterrows():
        icon = Icon(
                color="red",
                prefix="fa",
                icon=f"fa-building")
        Marker(
            location=row[["Latitude","Longitude"]],
            tooltip=row["Name"],
            icon=icon
        ).add_to(m)
m

In [92]:
for i, row in chosen_offices.iterrows():        
        icon = Icon(
                color="green",
                prefix="fa",
                icon=f"fa-coffee")
        Marker(
            location=row[["Starbucks Latitude","Starbucks Longitude"]],
            icon=icon
        ).add_to(m)
m

In [ ]:
for i, row in chosen_offices.iterrows():        
        icon = Icon(
                color="blue",
                prefix="fa",
                icon=f"fa-plane")
        Marker(
            location=row[["Airport Latitude","Airport Longitude"]],
            icon=icon
        ).add_to(m)
m

In [ ]:
for i, row in chosen_offices.iterrows():        
        icon = Icon(
                color="orange",
                prefix="fa",
                icon=f"fa-child")
        Marker(
            location=row[["School Latitude","School Longitude"]],
            icon=icon
        ).add_to(m)
m

In [90]:
m

In [83]:
mapping(icon="building")
mapping(req="Starbucks ", icon="building", color="green")
mapping(req="Airport ", icon="plane", color="blue")
mapping(req="School ", icon="child", color="orange")
m

# Chosen Office:   
  
### PicApp: ( 37.794020, -122.403124)

In [65]:
m = Map(location=[37.794020, -122.403124],zoom_start=5.5)
m

In [ ]:
m = Map(location=[37.794020, -122.403124],zoom_start=4)
for i, row in capitals.iterrows():
    if row["population"] > 2e5: 
        icon = Icon(
                color="red",
                prefix="fa",
                icon="trophy"
            )
    else:
        icon = Icon(
                color="green",
                prefix="fa",
                icon="paw"
            )
    Marker(
        location=row[["latitude","longitude"]],
        tooltip=row["state"],
        popup=row["capital"],
        icon=icon
    ).add_to(m)
m